In [1]:
import pandas as pd
import re
from tqdm import tqdm
tqdm.pandas()
from utils.DBReader import read_table, insert_dataframe,update_table,upsert_dataframe

### 1. Load eth node data (need to access through trusted ip address)

In [2]:
data = read_table(db_connection = 'conn9', table = 'eth_pow_nodes', all_col = True)

#### 1.1 Extract region information

In [3]:
patterns = [
    (re.compile(r'hz(/d+)?/', re.IGNORECASE), 'china'),
    (re.compile(r'cn',re.IGNORECASE),'china'),
    (re.compile(r'sz(/d+)?/',re.IGNORECASE),'china'),
    (re.compile(r'zj',re.IGNORECASE),'china'),
    (re.compile(r'(^|\W)ru',re.IGNORECASE),'russia'),
    (re.compile(r'sg',re.IGNORECASE),'singapore'),
    (re.compile(r'us-e',re.IGNORECASE),'us-east'),
    (re.compile(r'us-w',re.IGNORECASE),'us-west'),
    (re.compile(r'(^|\W)us',re.IGNORECASE),'us'),
    (re.compile(r'usa',re.IGNORECASE),'us'),
    (re.compile(r'eu(rope)?-n',re.IGNORECASE),'europe-north'),
    (re.compile(r'eu(rope)?-w',re.IGNORECASE),'europe-west'),
    (re.compile(r'seo',re.IGNORECASE),'south korea'),
    (re.compile(r'sing',re.IGNORECASE),'singapore'),
    (re.compile(r'(^|[^r])eu',re.IGNORECASE),'europe'),
    (re.compile(r'(^|\W)ua',re.IGNORECASE),'ukraine'),
    (re.compile(r'asia-e',re.IGNORECASE),'asia-east'),
    (re.compile(r'asia',re.IGNORECASE),'asia'),
    (re.compile(r'ca',re.IGNORECASE),'canada'),
    (re.compile(r'(?!spider)\bde\b',re.IGNORECASE),'germany'),
    (re.compile(r'jp',re.IGNORECASE),'japan'),
    (re.compile(r'(^|\W)tw',re.IGNORECASE),'taiwan'),
    (re.compile(r'(^|\W)se', re.IGNORECASE), 'sweden')
]

def determine_location(extra_data):
    if extra_data is not None:
        for pattern, pattern_label in patterns:
            if pattern.search(extra_data):
                pattern_counts[pattern_label] += 1
                return pattern_label
    pattern_counts['others'] += 1
    return 'others'

# Initialize the pattern counts dictionary
pattern_counts = {label: 0 for _, label in patterns}
pattern_counts['others'] = 0

# Determine locations
data['location'] = data['extra_data_ascii'].progress_apply(determine_location)

# Print the pattern counts
total_count = sum(pattern_counts.values())
print('Pattern counts:')
for label, count in pattern_counts.items():
    percentage = count / total_count * 100
    print(f'{label}: {count} ({percentage:.2f}%)')

100%|███████████████████████████████████████████████████████████████████| 15535775/15535775 [03:47<00:00, 68420.48it/s]

Pattern counts:
china: 1304055 (8.39%)
russia: 81560 (0.52%)
singapore: 173753 (1.12%)
us-east: 161823 (1.04%)
us-west: 80847 (0.52%)
us: 632544 (4.07%)
europe-north: 189658 (1.22%)
europe-west: 265229 (1.71%)
south korea: 232346 (1.50%)
europe: 1797808 (11.57%)
ukraine: 24430 (0.16%)
asia-east: 344725 (2.22%)
asia: 496934 (3.20%)
canada: 33422 (0.22%)
germany: 61564 (0.40%)
japan: 1983 (0.01%)
taiwan: 53789 (0.35%)
sweden: 14886 (0.10%)
others: 9584419 (61.69%)


#### 1.2 match miner address

In [4]:
path = 'Data/updated-ccaf-miner-address-region.xlsx'
miner = pd.read_excel(path)

In [5]:
#exclude miner address that wasn't in McDonald's paper
miner = miner[pd.notnull(miner['matched'])]

#standardize value to add up to 1
#miner['total'] = miner['europe'] +miner['us']+miner['asia']+miner['china']+miner['russia'] +miner['unknown']
region_list = ['europe','us','europe-west','europe-east','north-america','asia-east','asia','china','russia','unknown']

miner['total'] = 0
for region in region_list:
    miner[region] = miner[region].fillna(0)

for region in region_list:
    miner['total'] = miner['total'] + miner[region]
for region in region_list:
    miner[region] = miner[region]/miner['total']
miner.drop(['url','matched','total','description'],axis = 1,inplace = True)
miner.rename({'unknown':'others'},axis = 1,inplace = True)
print(miner.shape)
data.rename({'miner':'address'},axis = 1,inplace = True)
#merge miner to blocks
data_merged = pd.merge(data, miner, how = 'left',on = 'address')

#print in general how many blocks have been recognized
filt = (pd.notnull(data_merged['miner'])) | (data_merged['location']!='others')
est = round(data_merged.loc[filt].shape[0]/data_merged.shape[0]*100,2)
print(f'There are {data_merged.shape[0]} blocks in total, among them {est}% can be assigned to regions')

(101, 12)
There are 15535775 blocks in total, among them 91.03% can be assigned to regions


#### 1.3 assign region use both extra hex data and miner location

In [6]:
#creat dictionary to store all the info
def assign_region_monthly(df, time_col, region_col, miner_col):
    miner_region = ['europe','us','asia','china','russia','others']
    df[time_col] = pd.to_datetime(df[time_col])
    df['year'] = df[time_col].dt.year
    df['month'] = df[time_col].dt.month
    df['monthly-time'] = df['year'].astype('str') +'-'+ df['month'].astype('str') 
    storage = {}
    for time in df['monthly-time'].unique():
        storage[time] = {}
        storage[time]['total'] = 0
        for region in df[region_col].unique():
            storage[time][region] = 0
    for index, row in tqdm(df.iterrows(), total=df.shape[0]):
        #check if location info is available
        if row[region_col]!= 'others':
            storage[row['monthly-time']][row[region_col]] += 1
            storage[row['monthly-time']]['total'] +=1
        #check if miner info is available
        elif pd.notnull(row[miner_col]):
            storage[row['monthly-time']]['total'] +=1
            for m_region in miner_region:
                if row[m_region]>0:
                    storage[row['monthly-time']][m_region] += row[m_region]
        else:
            storage[row['monthly-time']]['others']+=1
            storage[row['monthly-time']]['total'] +=1
    df = df.drop(['year','month','monthly-time'],axis = 1)
    return storage

In [7]:
def assign_region_daily(df, time_col, region_col, miner_col):
    miner_region = ['europe','us','europe-west','europe-east','north-america',
                    'asia-east','asia','china','russia','others']

    # Convert the time column to just date format
    df['daily-time'] = df[time_col]

    # Initialize storage with zeros
    unique_times = df['daily-time'].unique()
    unique_regions = df[region_col].unique()
    storage = {}
    for time in unique_times:
        storage[time] = {}
        storage[time]['total'] = 0
        for region in unique_regions:
            storage[time][region] = 0
        for region_ in miner_region:
            storage[time][region_] = 0

    print("Processing region counts...")
    # Count for region_col (not 'others')
    region_counts = df[df[region_col] != 'others'].groupby(['daily-time', region_col]).size().reset_index(name='counts')

    for _, row in tqdm(region_counts.iterrows(), total=region_counts.shape[0]):
        storage[row['daily-time']][row[region_col]] = row['counts']
        storage[row['daily-time']]['total'] += row['counts']

    print("Processing miner counts...")
    # Count for miner_col
    miner_df = df[(df[miner_col].notnull()) & (df[region_col] == 'others')]
    
    for m_region in tqdm(miner_region):
        miner_counts = miner_df.groupby('daily-time')[m_region].sum()
        for time, count in miner_counts.iteritems():
            storage[time][m_region] += count
            storage[time]['total'] += count

    print("Processing 'others' counts...")
    # Count for 'others'
    others_count = df[(df[region_col] == 'others') & (df[miner_col].isnull())].groupby('daily-time').size()
    for time, count in tqdm(others_count.iteritems(), total=others_count.shape[0]):
        storage[time]['others'] += count
        storage[time]['total'] += count

    return storage


In [8]:
#aggregate on a monthly level
region_output = assign_region_daily(data_merged, 'time', 'location', 'miner')
#region_output = assign_region_monthly(data_merged, 'time', 'location', 'miner')

Processing region counts...


100%|█████████████████████████████████████████████████████████████████████████| 22918/22918 [00:01<00:00, 16401.26it/s]


Processing miner counts...


  0%|                                                                                           | 0/10 [00:00<?, ?it/s]C:\Users\clair\AppData\Local\Temp\ipykernel_385184\1624177744.py:34: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for time, count in miner_counts.iteritems():
 10%|████████▎                                                                          | 1/10 [00:00<00:08,  1.05it/s]C:\Users\clair\AppData\Local\Temp\ipykernel_385184\1624177744.py:34: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for time, count in miner_counts.iteritems():
 20%|████████████████▌                                                                  | 2/10 [00:01<00:07,  1.05it/s]C:\Users\clair\AppData\Local\Temp\ipykernel_385184\1624177744.py:34: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for time, count in miner_counts.iteritem

Processing 'others' counts...


C:\Users\clair\AppData\Local\Temp\ipykernel_385184\1624177744.py:41: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for time, count in tqdm(others_count.iteritems(), total=others_count.shape[0]):
100%|██████████████████████████████████████████████████████████████████████████| 2604/2604 [00:00<00:00, 372026.96it/s]


In [9]:
#convert dictionary to dataframe
df_list = []
for key, value in region_output.items():
    value['time'] =key
    df_list.append(value)
region_count = pd.DataFrame(df_list)
col_order = ['time','china', 'asia-east', 'asia', 'europe', 'europe-west',
             'europe-north', 'europe-east','north-america','us','us-east', 'us-west', 'singapore',
             'ukraine', 'russia',  'canada', 'sweden','japan','taiwan',
             'germany', 'south korea', 'others', 'total']
region_count = region_count[col_order]
#region_count.to_excel("Output/region_count.xlsx",index = False)
region_count.to_excel("Output/updated_daily_region_count.xlsx",index = False)

In [10]:
#standardize to percentage
region_percent = region_count.copy()
for col in col_order[1:-1]:
    region_percent[col] = region_percent[col]/region_percent['total']
#region_percent.to_excel("Output/region_percent.xlsx",index = False)
region_percent.to_excel("Output/updated_daily_region_percent.xlsx",index = False)

#### 1.4 visualize node distribution change

In [35]:
region_percent = pd.read_excel('Output/updated_daily_region_percent.xlsx')

In [36]:
import plotly.graph_objects as go
fig = go.Figure()
fig.update_layout(
        title = 'ETH PoW Mining Geographic Distribution Evolution')
color = ['#fe4a49', '#2ab7ca', '#fed766', '#e6e6ea', '#03396c', '#005b96', '#6497b1', '#b3cde0','#FF6347 ',
'#20B2AA ','#FFD700 ','#7FFFD4 ','#DDA0DD ','#4169E1 ','#F08080 ','#90EE90 ','#AFEEEE ','#DB7093 ','#808080 ','#d9ead3','#def3f6']

for index, col in enumerate(list(region_percent.columns[1:-1])):
    fig.add_trace(go.Scatter(
    x=region_percent['time'], 
    y=region_percent[col],
    mode='lines',
    fillcolor = color[index],
    line=dict(width=0.5),
    stackgroup='one',
    name = col,groupnorm='percent'
))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
        type='linear',
        range=[1, 100],
        ticksuffix='%'))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
            title='Share of Geographic Distribution'))

fig.write_image(file = 'Graph/ETH PoW Mining Geographic Distribution Evolution.jpg',format="jpg", engine="kaleido",
               width = 1000,
               height = 600)
fig.show()

In [37]:
broad_region_dict= {'asia inclusive': ['china','asia-east','asia','singapore','japan','taiwan','south korea'],
               'europe inclusive':['europe', 'europe-east','europe-west', 'europe-north','ukraine','russia','sweden','germany'],
               'north amercia inclusive':['us','north-america', 'us-east', 'us-west','canada'],
               'others inclusive':['others']
}

broad_region = region_percent.copy()
for key in broad_region_dict.keys():
    broad_region[key] = 0
for key, value in broad_region_dict.items():
    for region in value: # iterate different broad region
        broad_region[key] += broad_region[region]
reserve_col = ['time']
reserve_col.extend(broad_region_dict.keys())
broad_region = broad_region[reserve_col]
broad_region.rename({'asia inclusive': 'Asia',
               'europe inclusive':'Europe',
               'north amercia inclusive':'North Ameria',
               'others inclusive':'Others'},axis = 1,inplace = True)
broad_region.to_excel("Output/broader_region_percent.xlsx",index = False)

In [38]:
import plotly.graph_objects as go
fig = go.Figure()
fig.update_layout(
        title = 'ETH PoW Mining Geographic Distribution Evolution')
color = ['#fe4a49', '#2ab7ca', '#fed766', '#e6e6ea', '#03396c', '#005b96', '#6497b1', '#b3cde0','#FF6347 ',
'#20B2AA ','#FFD700 ','#7FFFD4 ','#DDA0DD ','#4169E1 ','#F08080 ','#90EE90 ','#AFEEEE ','#DB7093 ','#808080 ']

for index, col in enumerate(list(broad_region.columns[1:])):
    fig.add_trace(go.Scatter(
    x=broad_region['time'], 
    y=broad_region[col],
    mode='lines',
    fillcolor = color[index],
    line=dict(width=0.5),
    stackgroup='one',
    name = col,groupnorm='percent'
))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
        type='linear',
        range=[1, 100],
        ticksuffix='%'))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
            title='Share of Geographic Distribution'))

fig.write_image(file = 'Graph/ETH PoW Mining Geographic Distribution Evolution (Broader Region).jpg',format="jpg", engine="kaleido",
               width = 1000,
               height = 600)
fig.show()

### btc comparison

In [32]:
pd.set_option('display.max_rows',200)

In [33]:
mining_map_countries = read_table(db_connection='custom_data',table='mining_map_countries',schemas = None, all_col = True) # Node Share CBECI Mining Map of all countries
mining_map_countries.rename({'value':'btc miner share','date':'time'},axis = 1,inplace = True)
mining_map_countries['time'] =pd.to_datetime(mining_map_countries['time'])
mining_map_countries.drop('id',axis = 1,inplace = True)


In [34]:
folder = 'data/'
country_classification = pd.read_excel(folder+'country_classification_clean.xlsx')
country_classification = country_classification.drop_duplicates(['country_id'])

In [37]:
btc_map[btc_map['time'] == '2021-07-01']

name  btc miner share       time  country_id  region  \
22      Hong Kong SAR, China     2.727000e-04 2021-07-01          61    asia   
2601          Mainland China     0.000000e+00 2021-07-01         129    asia   
2602                Slovakia     1.053980e-04 2021-07-01         185  europe   
2604                  Brunei     1.897860e-03 2021-07-01         116    asia   
2605                  Taiwan     2.728380e-04 2021-07-01         100    asia   
2606              Kyrgyzstan     7.169730e-04 2021-07-01          64    asia   
2607               Venezuela     6.350050e-03 2021-07-01         108  others   
2608                    Laos     3.709600e-05 2021-07-01          65    asia   
2610   Republic of the Congo     1.832200e-04 2021-07-01          87  others   
2611                 Lebanon     4.175040e-05 2021-07-01         190    asia   
2612                 Bahrain     3.276230e-05 2021-07-01         109    asia   
2815              Luxembourg     2.472650e-05 2021-07-01          72  europe   
2816               Mauritius     2.620630e-05 2021-07-01          25  others   
2817                    Peru     1.189270e-05 2021-07-01          86  others   
2818               Guatemala     2.809580e-05 2021-07-01          46  others   
2819             New Zealand     2.783860e-05 2021-07-01          83  others   
2820                 Nigeria     2.455370e-05 2021-07-01         175  others   
2821                 Ecuador     1.230540e-05 2021-07-01          49  others   
2822  Bosnia and Herzegovina     1.671060e-05 2021-07-01         119  europe   
2823                  Cyprus     1.657970e-05 2021-07-01          16    asia   
2824                    Iraq     1.599220e-05 2021-07-01         148    asia   
2825                   Chile     1.568590e-05 2021-07-01         157  others   
2826                   Sudan     1.359900e-05 2021-07-01         204  others   
2827              Bangladesh     2.876350e-05 2021-07-01         111    asia   
2828                  Panama     1.764500e-05 2021-07-01         169  others   
2829                  Latvia     3.166850e-05 2021-07-01          28  europe   
2830             Philippines     3.425390e-05 2021-07-01         178    asia   
2831                Slovenia     3.546490e-05 2021-07-01          99  europe   
2832                 Denmark     3.725020e-05 2021-07-01         156  europe   
2833                 Austria     4.594090e-05 2021-07-01         106  europe   
2834         North Macedonia     4.715240e-05 2021-07-01         105  europe   
2835    United Arab Emirates     6.076330e-05 2021-07-01         211    asia   
2836                  Israel     6.338500e-05 2021-07-01         150    asia   
2837                 Albania     6.389840e-05 2021-07-01          24  europe   
2838                 Morocco     7.162230e-05 2021-07-01         170  others   
2839            Turkmenistan     8.222590e-05 2021-07-01         198    asia   
2840                  Kosovo     8.964350e-05 2021-07-01         216  others   
2841               Lithuania     3.234920e-05 2021-07-01         192  europe   
2842                  Zambia     0.000000e+00 2021-07-01         209  others   
2843                   Malta     0.000000e+00 2021-07-01          76  europe   
2844                Tanzania     9.301290e-06 2021-07-01         103  others   
2845             El Salvador     0.000000e+00 2021-07-01         139  others   
2846                  Bhutan     0.000000e+00 2021-07-01          33    asia   
2847                Barbados     0.000000e+00 2021-07-01          39  others   
2848                  Uganda     1.974390e-09 2021-07-01         107  others   
2849                  Jordan     7.797930e-09 2021-07-01          68    asia   
2850                Cambodia     1.168580e-08 2021-07-01         125    asia   
2851                 Uruguay     1.850610e-08 2021-07-01         122  others   
2852                 Bermuda     9.553480e-08 2021-07-01         113  others   
2853                    

In [35]:
btc_map = pd.merge(mining_map_countries,country_classification, how = 'left', on = 'country_id')
btc_map['region'] = btc_map['region'].fillna('others')

broad_region_dict= {'Asia': ['china','asia-east','asia','singapore','japan','taiwan','south korea'],
               'Europe':['europe', 'europe-east','europe-west', 'europe-north','ukraine','russia','sweden','germany'],
               'North Ameria':['us','north-america', 'us-east', 'us-west','canada'],
               'Others':['others']
}

def get_broad_region(value):
    for broad_region, countries in broad_region_dict.items():
        if value in countries:
            return broad_region
    return None

btc_map['broad_region'] = btc_map['region'].apply(get_broad_region)

aggregate_btc_map = btc_map.groupby(['time','broad_region'],as_index = False)['btc miner share'].sum()
aggregate_btc_map = pd.pivot(aggregate_btc_map,index = 'time', columns = 'broad_region', values = 'btc miner share')
aggregate_btc_map = aggregate_btc_map.reset_index(drop = False)

In [36]:
import plotly.graph_objects as go
fig = go.Figure()
fig.update_layout(
        title = 'BTC Mining Geographic Distribution Evolution')
color = ['#fe4a49', '#2ab7ca', '#fed766', '#e6e6ea', '#03396c', '#005b96', '#6497b1', '#b3cde0','#FF6347 ',
'#20B2AA ','#FFD700 ','#7FFFD4 ','#DDA0DD ','#4169E1 ','#F08080 ','#90EE90 ','#AFEEEE ','#DB7093 ','#808080 ']

for index, col in enumerate(list(aggregate_btc_map.columns[1:])):
    fig.add_trace(go.Scatter(
    x=aggregate_btc_map['time'], 
    y=aggregate_btc_map[col],
    mode='lines',
    fillcolor = color[index],
    line=dict(width=0.5),
    stackgroup='one',
    name = col,groupnorm='percent'
))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
        type='linear',
        range=[1, 100],
        ticksuffix='%'))

fig.update_layout(
    showlegend=True,
    yaxis=dict(
            title='Share of Geographic Distribution'))

fig.write_image(file = 'Graph/ETH PoW Mining Geographic Distribution Evolution (Broader Region).jpg',format="jpg", engine="kaleido",
               width = 1000,
               height = 600)
fig.show()